In [1]:

import cv2
import numpy as np
import time
import timeit
from pathlib import Path
import csv

In [2]:
def load_landmarks(lm_path):
    """
    Loads the landmarks from the given path.
    
    lm_path: Path object to the landmarks file
    
    Return: a dict - key: frame number, value: np.array of landmarks (68,2)
    """
    with open(lm_path) as f:
        next(f) # skip the first line
        reader = csv.reader(f, delimiter=',')
        lines = np.array(list(reader))

    frames = lines[:,0].astype(np.uint16)
    landmarks = lines[:,1:].reshape(-1,68,2).astype(np.float32)     # (n_frames, n_landmarks, 2)
    return frames, landmarks


In [3]:
def load_bboxes(bbox_path):
    """
    Loads the bounding boxes from the given path.
    
    bbox_path: Path object to the bounding boxes file
    
    Return: a dict - key: frame number, value: np.array of bounding boxes (n_bboxes, 4)
    """
    with open(bbox_path) as f:
        next(f) # skip the first line
        reader = csv.reader(f, delimiter=',')
        lines = np.array(list(reader))

    frames = lines[:,0]
    bboxes = lines[:,1:].reshape(-1,4).astype(np.float32)     # (n_frames, n_bboxes, 4)
    return frames, bboxes

In [4]:
lm_path = Path("./NeuroFace_Open_Access_Data/ALS/Landmarks_gt/")
bbox_path = Path("./NeuroFace_Open_Access_Data/ALS/Bbox_gt/")

In [5]:
lm_paths = [f for f in Path(lm_path).iterdir() if f.is_file()]  # landmarks paths, return type is WindowsPath or PosixPath
bbox_paths = [f for f in Path(bbox_path).iterdir() if f.is_file()]  # bounding box paths, return type is WindowsPath or PosixPath
lm_paths_str = [str(f) for f in lm_paths]

In [6]:
lm_filenames = [f.name for f in lm_paths] # landmarks filenames
lm_filenames[0:5]

['A002_02_BBP_NORMAL_color.txt',
 'A002_02_DDK_PATAKA_color.txt',
 'A002_02_DDK_PA_color.txt',
 'A002_02_NSM_BLOW_color.txt',
 'A002_02_NSM_KISS_color.txt']

In [7]:
patients_id = [f[0:4] for f in lm_filenames] # get first 4 characters of filename
patients = {p:{} for p in patients_id}
for p in patients:  
    print('Patient:', p) 
    # Every patient has a dictionary of tasks, each task has a dict of frames, which contains dict of landmarks and bboxes
    tasks = ['_'.join(t.split('_')[2:4]) for t in lm_filenames if t[0:4]==p] # list of tasks for patient p
    #tasks_lm_path = [lm_paths[lm_filenames.index('_'.join((p,'02',t,'color.txt')))] for t in tasks]
    #tasks_bbox_path = [bbox_paths[lm_filenames.index('_'.join((p,'02',t,'color.txt')))] for t in tasks]
    #tasks_lm_path = [lm_paths[lm_filenames.index('_'.join((p,'02',t,'color.txt')))] for t in tasks]
    #tasks_bbox_path = [bbox_paths[lm_filenames.index('_'.join((p,'02',t,'color.txt')))] for t in tasks]
                
    patients[p] = {t:{} for t in tasks}
    
    #for i in range(len(tasks)):
    for t in tasks:
        # for every task, load the landmarks and bboxes
        this_filename = '_'.join((p,'02',t,'color.txt'))
        cur_lm_path = lm_path / this_filename
        cur_bbox_path = bbox_path / this_filename
        
        frames, landmarks = load_landmarks(cur_lm_path)
        _, bboxes = load_bboxes(cur_bbox_path)

        patients[p][t] = {f:{} for f in frames} # now we have a dict of frames

        # need to fill every frame's dict with landmarks and bboxes, and also have a spot for image
        for f in frames:
            idx = np.where(frames==f)[0][0]
            print('Frame:', f)
            img_path = Path("./NeuroFace_Open_Access_Data/ALS/Frames/") / '_'.join((p,'02',t,'color.avi',str(f)+'.jpg'))
            print(img_path)
            patients[p][t][f]['landmarks'] = landmarks[idx]
            patients[p][t][f]['bbox'] = bboxes[idx]
            patients[p][t][f]['image'] = cv2.imread(str(img_path))
            print(patients[p][t][f])
       

Patient: A002
Frame: 159
NeuroFace_Open_Access_Data\ALS\Frames\A002_02_BBP_NORMAL_color.avi_159.jpg
{'landmarks': array([[192.07207, 216.75676],
       [185.40541, 231.53152],
       [182.7027 , 247.56757],
       [183.80952, 265.     ],
       [188.09525, 282.61905],
       [196.90475, 298.09525],
       [207.61905, 309.5238 ],
       [223.09525, 319.2857 ],
       [246.66667, 325.7143 ],
       [270.81082, 329.18918],
       [294.0476 , 326.1905 ],
       [312.38095, 320.2381 ],
       [327.85715, 309.2857 ],
       [337.85715, 293.33334],
       [345.4762 , 273.8095 ],
       [349.5238 , 253.33333],
       [350.     , 235.     ],
       [216.21622, 172.79279],
       [224.68468, 167.92793],
       [234.23424, 165.76576],
       [245.04504, 165.58559],
       [254.77478, 166.66667],
       [290.0901 , 168.28828],
       [299.27927, 169.009  ],
       [308.46848, 171.17117],
       [316.93695, 174.05405],
       [326.12613, 179.63963],
       [269.3066 , 191.15398],
       [268.1408 ,

In [8]:
frames[frames==140]


array([140], dtype=uint16)

In [9]:
patients['A002']['BBP_NORMAL']

{159: {'landmarks': array([[192.07207, 216.75676],
         [185.40541, 231.53152],
         [182.7027 , 247.56757],
         [183.80952, 265.     ],
         [188.09525, 282.61905],
         [196.90475, 298.09525],
         [207.61905, 309.5238 ],
         [223.09525, 319.2857 ],
         [246.66667, 325.7143 ],
         [270.81082, 329.18918],
         [294.0476 , 326.1905 ],
         [312.38095, 320.2381 ],
         [327.85715, 309.2857 ],
         [337.85715, 293.33334],
         [345.4762 , 273.8095 ],
         [349.5238 , 253.33333],
         [350.     , 235.     ],
         [216.21622, 172.79279],
         [224.68468, 167.92793],
         [234.23424, 165.76576],
         [245.04504, 165.58559],
         [254.77478, 166.66667],
         [290.0901 , 168.28828],
         [299.27927, 169.009  ],
         [308.46848, 171.17117],
         [316.93695, 174.05405],
         [326.12613, 179.63963],
         [269.3066 , 191.15398],
         [268.1408 , 199.31598],
         [266.48544, 207.

In [10]:
[*patients['A017'].keys()]

['BBP_NORMAL',
 'DDK_PATAKA',
 'DDK_PA',
 'NSM_BIGSMILE',
 'NSM_BROW',
 'NSM_KISS',
 'NSM_OPEN',
 'NSM_SPREAD']

In [11]:
from pathlib import Path
import pandas as pd
import os 
p = Path("./NeuroFace_Open_Access_Data/ALS/Landmarks_gt").glob('**/*')
p = list(p)
p[0].name

'A002_02_BBP_NORMAL_color.txt'

In [12]:
with open(p[0]) as f:
    next(f) # skip the first line
    reader = csv.reader(f, delimiter=',')
    lines = np.array(list(reader))
    
frames = lines[:,0]
landmarks = lines[:,1:].reshape(-1,68,2).astype(np.float32) 

In [13]:
landmarks[3]

array([[190.2381 , 221.66667],
       [185.71428, 236.42857],
       [184.28572, 254.28572],
       [185.2381 , 273.09525],
       [189.28572, 292.14285],
       [198.33333, 309.7619 ],
       [211.90475, 322.85715],
       [231.42857, 332.14285],
       [255.     , 336.42856],
       [276.42856, 337.14285],
       [300.4762 , 330.     ],
       [317.85715, 320.7143 ],
       [331.90475, 306.66666],
       [339.7619 , 289.2857 ],
       [345.4762 , 272.85715],
       [350.2381 , 255.     ],
       [349.2857 , 238.33333],
       [216.03604, 174.41441],
       [225.76576, 171.17117],
       [234.95496, 169.90991],
       [244.14415, 169.90991],
       [253.51352, 170.8108 ],
       [292.7928 , 171.35135],
       [301.44144, 171.89189],
       [309.72974, 173.51352],
       [318.73874, 176.03604],
       [326.66666, 179.81982],
       [270.0838 , 196.89551],
       [269.1671 , 205.27783],
       [268.0722 , 213.39008],
       [266.79068, 221.69077],
       [246.3063 , 241.26126],
       [

In [14]:
a = a[1:]
a.shape

NameError: name 'a' is not defined

In [ ]:
a[0][1:].reshape(-1,2).astype(np.float32) 

array([[192.07207, 216.75676],
       [185.40541, 231.53152],
       [182.7027 , 247.56757],
       [183.80952, 265.     ],
       [188.09525, 282.61905],
       [196.90475, 298.09525],
       [207.61905, 309.5238 ],
       [223.09525, 319.2857 ],
       [246.66667, 325.7143 ],
       [270.81082, 329.18918],
       [294.0476 , 326.1905 ],
       [312.38095, 320.2381 ],
       [327.85715, 309.2857 ],
       [337.85715, 293.33334],
       [345.4762 , 273.8095 ],
       [349.5238 , 253.33333],
       [350.     , 235.     ],
       [216.21622, 172.79279],
       [224.68468, 167.92793],
       [234.23424, 165.76576],
       [245.04504, 165.58559],
       [254.77478, 166.66667],
       [290.0901 , 168.28828],
       [299.27927, 169.009  ],
       [308.46848, 171.17117],
       [316.93695, 174.05405],
       [326.12613, 179.63963],
       [269.3066 , 191.15398],
       [268.1408 , 199.31598],
       [266.48544, 207.39532],
       [264.44464, 215.61224],
       [243.42342, 236.03604],
       [

In [ ]:

d = pd.read_csv(p[0], sep=', ', engine='python')
d

Frame          x1          y1          x2          y2          x3  \
0     159  192.072072  216.756757  185.405405  231.531532  182.702703   
1     446  192.380952  220.000000  186.190476  236.666667  185.000000   
2     455  190.952381  223.095238  185.952381  236.666667  184.523810   
3     476  190.238095  221.666667  185.714286  236.428571  184.285714   
4     184  189.761905  217.380952  185.952381  234.761905  185.000000   
5     204  187.857143  223.809524  185.714286  238.571429  185.238095   
6     209  187.857143  222.857143  184.761905  240.000000  184.285714   
7     232  186.428571  230.476190  184.523810  245.952381  184.523810   
8     280  187.857143  226.428571  185.000000  241.666667  185.238095   
9     305  189.761905  222.857143  185.238095  238.809524  185.000000   
10    325  189.047619  223.333333  185.714286  238.809524  185.000000   
11    332  188.571429  223.571429  185.238095  239.523810  185.000000   
12    355  189.285714  225.238095  186.190476  240.238095  186.428571   
13    399  189.523810  223.333333  185.714286  238.809524  185.000000   
14    427  190.476190  221.666667  185.952381  237.857143  184.523810   

            y3          x4          y4          x5  ...         x64  \
0   247.567568  183.809524  265.000000  188.095238  ...  271.531532   
1   253.809524  186.190476  273.571429  190.000000  ...  275.675676   
2   253.809524  185.045045  270.630631  189.047619  ...  272.792793   
3   254.285714  185.238095  273.095238  189.285714  ...  274.774775   
4   251.428571  187.380952  270.238095  192.857143  ...  265.714286   
5   255.714286  187.857143  271.904762  192.619048  ...  271.428571   
6   256.904762  187.619048  273.095238  192.619048  ...  271.666667   
7   265.000000  186.428571  282.857143  192.857143  ...  273.333333   
8   258.333333  188.095238  273.571429  193.095238  ...  272.380952   
9   256.428571  187.142857  273.095238  192.857143  ...  269.523810   
10  256.190476  186.666667  273.095238  190.476190  ...  277.380952   
11  256.666667  187.380952  273.809524  193.809524  ...  273.333333   
12  257.619048  188.571429  275.238095  194.047619  ...  272.857143   
13  255.476190  185.952381  274.523810  191.666667  ...  273.809524   
14  256.666667  186.190476  275.714286  191.190476  ...  270.238095   

           y64         x65         y65         x66         y66         x67  \
0   262.342342  284.355917  269.031850  270.810811  264.684685  258.738739   
1   263.963964  285.765766  274.774775  272.972973  273.153153  259.819820   
2   268.288288  287.747748  272.792793  273.333333  265.945946  260.540541   
3   271.711712  287.207207  280.720721  273.153153  280.000000  260.360360   
4   257.619048  274.523810  262.380952  266.190476  264.285714  258.809524   
5   266.666667  280.952381  273.095238  271.190476  270.952381  258.333333   
6   265.476190  286.190476  271.904762  271.190476  266.904762  257.380952   
7   271.904762  285.952381  280.000000  273.809524  281.904762  260.476190   
8   264.285714  286.904762  270.952381  272.380952  264.761905  260.952381   
9   261.428571  276.428571  265.000000  269.047619  266.428571  259.523810   
10  263.571429  286.904762  272.142857  277.142857  271.904762  260.238095   
11  264.523810  287.142857  270.476190  273.095238  266.190476  259.523810   
12  266.904762  281.904762  274.047619  272.142857  275.714286  258.571429   
13  264.285714  286.666667  270.000000  273.333333  265.476190  258.809524   
14  262.142857  277.142857  265.714286  270.476190  265.476190  259.523810   

           y67         x68         y68  
0   263.243243  246.486486  263.063063  
1   271.711712  247.027027  270.090090  
2   265.945946  248.648649  265.585586  
3   278.378378  247.747748  277.117117  
4   265.000000  250.238095  263.333333  
5   269.285714  247.619048  268.809524  
6   264.047619  245.476190  262.142857  
7   279.285714  246.190476  277.380952  
8   264.047619  248.333333  263.571429  
9   265.714286  249.761905  264.761905 

In [ ]:
d.T

0           1           2           3           4           5   \
Frame  159.000000  446.000000  455.000000  476.000000  184.000000  204.000000   
x1     192.072072  192.380952  190.952381  190.238095  189.761905  187.857143   
y1     216.756757  220.000000  223.095238  221.666667  217.380952  223.809524   
x2     185.405405  186.190476  185.952381  185.714286  185.952381  185.714286   
y2     231.531532  236.666667  236.666667  236.428571  234.761905  238.571429   
...           ...         ...         ...         ...         ...         ...   
y66    264.684685  273.153153  265.945946  280.000000  264.285714  270.952381   
x67    258.738739  259.819820  260.540541  260.360360  258.809524  258.333333   
y67    263.243243  271.711712  265.945946  278.378378  265.000000  269.285714   
x68    246.486486  247.027027  248.648649  247.747748  250.238095  247.619048   
y68    263.063063  270.090090  265.585586  277.117117  263.333333  268.809524   

               6           7           8           9           10          11  \
Frame  209.000000  232.000000  280.000000  305.000000  325.000000  332.000000   
x1     187.857143  186.428571  187.857143  189.761905  189.047619  188.571429   
y1     222.857143  230.476190  226.428571  222.857143  223.333333  223.571429   
x2     184.761905  184.523810  185.000000  185.238095  185.714286  185.238095   
y2     240.000000  245.952381  241.666667  238.809524  238.809524  239.523810   
...           ...         ...         ...         ...         ...         ...   
y66    266.904762  281.904762  264.761905  266.428571  271.904762  266.190476   
x67    257.380952  260.476190  260.952381  259.523810  260.238095  259.523810   
y67    264.047619  279.285714  264.047619  265.714286  269.285714  263.809524   
x68    245.476190  246.190476  248.333333  249.761905  246.428571  247.380952   
y68    262.142857  277.380952  263.571429  264.761905  267.619048  263.571429   

               12          13          14  
Frame  355.000000  399.000000  427.000000  
x1     189.285714  189.523810  190.476190  
y1     225.238095  223.333333  221.666667  
x2     186.190476  185.714286  185.952381  
y2     240.238095  238.809524  237.857143  
...           ...         ...         ...  
y66    275.714286  265.476190  265.476190  
x67    258.571429  258.809524  259.523810  
y67    273.333333  262.619048  265.238095  
x68    246.190476  246.666667  250.000000  
y68    272.857143  261.904762  264.047619  

[137 rows x 15 columns]

In [ ]:
for x, y in d.iterrows():
    print(y)
    break

n = list(d.iterrows())

Frame    159.000000
x1       192.072072
y1       216.756757
x2       185.405405
y2       231.531532
            ...    
y66      264.684685
x67      258.738739
y67      263.243243
x68      246.486486
y68      263.063063
Name: 0, Length: 137, dtype: float64


In [ ]:
patients = {}
# read in csv files of landmarks and bboxes
# for a single patient, there are 7 different tasks / poses
# for each task, there are multiple images (frames listed in the csv file)





In [ ]:
import csv
import re
with open(p[0]) as fp:
    reader = csv.reader(fp, delimiter=re.compile(r", "), quotechar='"')
    # next(reader, None)  # skip the headers
    data_read = [row for row in reader]

print(data_read[0])

TypeError: "delimiter" must be string, not re.Pattern

In [ ]:
from DatasetTester import DatasetTester

In [ ]:
a = DatasetTester("./NeuroFace_Open_Access_Data/ALS")

Patient: A002
Patient: A006
Patient: A008
Patient: A009
Patient: A010
Patient: A011
Patient: A012
Patient: A014
Patient: A015
Patient: A016
Patient: A017


In [ ]:
t = a._patients['A002']['BBP_NORMAL']
t[list(t.keys())[0]]

{'landmarks_gt': array([[192.07207, 216.75676],
        [185.40541, 231.53152],
        [182.7027 , 247.56757],
        [183.80952, 265.     ],
        [188.09525, 282.61905],
        [196.90475, 298.09525],
        [207.61905, 309.5238 ],
        [223.09525, 319.2857 ],
        [246.66667, 325.7143 ],
        [270.81082, 329.18918],
        [294.0476 , 326.1905 ],
        [312.38095, 320.2381 ],
        [327.85715, 309.2857 ],
        [337.85715, 293.33334],
        [345.4762 , 273.8095 ],
        [349.5238 , 253.33333],
        [350.     , 235.     ],
        [216.21622, 172.79279],
        [224.68468, 167.92793],
        [234.23424, 165.76576],
        [245.04504, 165.58559],
        [254.77478, 166.66667],
        [290.0901 , 168.28828],
        [299.27927, 169.009  ],
        [308.46848, 171.17117],
        [316.93695, 174.05405],
        [326.12613, 179.63963],
        [269.3066 , 191.15398],
        [268.1408 , 199.31598],
        [266.48544, 207.39532],
        [264.44464, 215.